In [0]:
# Fazer Pasta
# dbutils.fs.mkdirs(path)

# Remover Pasta/Arquivo
# dbutils.fs.rm(path, recurse=True)

In [0]:
%run
./06_entrypoints

  Obtaining dependency information for pip from https://files.pythonhosted.org/packages/ef/7d/500c9ad20238fcfcb4cb9243eede163594d7020ce87bd9610c9e02771876/pip-24.3.1-py3-none-any.whl.metadata
  Using cached pip-24.3.1-py3-none-any.whl.metadata (3.7 kB)
Using cached pip-24.3.1-py3-none-any.whl (1.8 MB)
  Attempting uninstall: pip
    Found existing installation: pip 23.2.1
    Uninstalling pip-23.2.1:
      Successfully uninstalled pip-23.2.1
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
  Using cached great_expectations-1.2.2-py3-none-any.whl.metadata (8.5 kB)
  Using cached altair-4.2.2-py3-none-any.whl.metadata (13 kB)
  Using cached jinja2-3.1.4-py3-none-any.whl.metadata (2.6 kB)
  Using cached jsonschema-4.23.0-py3-none-any.whl.metadata (7.9 kB)
  Using cached marshmallow-3.23.1-py3-none-any.whl.metadata (7.5 kB)
  Using cached mistune-3.0.2-py3-none-any.whl.metadata (1.7 kB)
  Using cached posthog-2.5.0-p

True

In [0]:
# Bibliotecas
from pyspark.sql.functions import *
from pyspark.sql.types import *
import great_expectations as gx
from datetime import date

# Raw & Bronze

## Calendar

In [0]:
df_raw_calendar = (spark.read.
                   option("multiline", "true").
                   option("quote", '"').
                   option("escape", '"').
                   csv(path_raw_calendar, header=True))
df_raw_calendar = df_raw_calendar.dropDuplicates()
df_raw_calendar.display()

In [0]:
df_raw_calendar.count()

In [0]:
df_raw_calendar.write.mode("overwrite").parquet(path_bronze_calendar)

## Listings

In [0]:
df_raw_listings = (spark.read.
               option("multiline", "true").
               option("quote", '"').
               option("escape", '"').
               csv(path_raw_listings, header=True))
df_raw_listings = df_raw_listings.dropDuplicates()
df_raw_listings.display()

In [0]:
df_raw_listings.count()

In [0]:
df_raw_listings.write.mode("overwrite").parquet(path_bronze_listings)

## Reviews

In [0]:
df_raw_reviews = (spark.read.
               option("multiline", "true").
               option("quote", '"').
               option("escape", '"').
               csv(path_raw_reviews, header=True))
df_raw_reviews = df_raw_reviews.dropDuplicates()
df_raw_reviews.display()

In [0]:
df_raw_reviews.count()

In [0]:
df_raw_reviews.write.mode("overwrite").parquet(path_bronze_reviews)

# Silver

## Calendar

In [0]:
df_calendar = spark.read.parquet(path_bronze_calendar)
df_calendar.display()

In [0]:
df_calendar.count() == 12652371

* listing_id - alterar para tipo LongType (Para integer gera muitos números nulos, LongType aceita um range maior de digitos)
* date - alterar para tipo datetime
* available - alterar t para True e f para False. Alterar tipo para booleano
* price - remover cifraão e virgulas. Alterar tipo para float
* minimum_nights - alterar para tipo integer
* maximum_nights - alterar para tipo integer

As conversões serão feitas e depois o schema vai ser informado como um todo.


In [0]:
df_new = (df_calendar
               .withColumn("listing_id", col("listing_id").cast(LongType()))
               .withColumn("date", to_date("date", "yyyy-MM-dd"))
               .withColumn("available", 
                           when(col("available") == "t", True).
                           when(col("available") == "f", False).
                           otherwise(None))
               .withColumn("price", regexp_replace(col("price"), "\\$", ""))
               .withColumn("price", regexp_replace(col("price"), ",", ""))
               .withColumn("price", col("price").cast("float"))
               .withColumn("minimum_nights", col("minimum_nights").cast("integer"))
               .withColumn("maximum_nights", col("maximum_nights").cast("integer")))

df_new.display()


In [0]:
df_calendar.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_calendar.columns]).display()

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_new.columns]).display()

In [0]:
df_calendar.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_calendar.columns]).display()

## Listings

In [0]:
df_listings = spark.read.parquet(path_bronze_listings)
df_listings.display()

In [0]:
# Colunas para remover strings: "\\$","\\%", ",", " "
tratar_antes = ["host_response_rate", "host_acceptance_rate", "price"]


numericos_int = ["host_id", "host_response_rate", "host_acceptance_rate" ,"host_listings_count", "host_total_listings_count", 
                 "accommodates", "bedrooms", "beds", "minimum_nights", "maximum_nights", "minimum_minimum_nights", 
                 "maximum_minimum_nights", "minimum_maximum_nights", "maximum_maximum_nights", "availability_30", 
                 "availability_60", "availability_90", "availability_365", "number_of_reviews", "number_of_reviews_ltm", 
                 "number_of_reviews_l30d", "calculated_host_listings_count", "calculated_host_listings_count_entire_homes", 
                 "calculated_host_listings_count_private_rooms", "calculated_host_listings_count_shared_rooms"]

numericos_float = ["latitude", "longitude", "bathrooms", "price", "minimum_nights_avg_ntm", "maximum_nights_avg_ntm", 
                   "review_scores_rating", "review_scores_accuracy", "review_scores_cleanliness", "review_scores_checkin", 
                   "review_scores_communication", "review_scores_location", "review_scores_value", "reviews_per_month"]

numericos_long = ["id", "scrape_id"]

colunas_data = ["last_scraped", "host_since", "calendar_last_scraped", "first_review", "last_review"]

booleanos = ["host_is_superhost", "host_has_profile_pic", "host_identity_verified", "has_availability", "instant_bookable"]

listas = ["host_verifications", "amenities"]

Iteração nas colunas para tratamento:

* tratar_antes - remover "%", "$" "," e " "
* numericos_int - Transformar int
* numericos_float - Transformar para float
* numericos_long - Transformar para LongType (como int gera muitos números nulos)
* colunas_data - Convertido para formato "yyyy-MM-dd"
* booleanos - Convertido para Booleano
* listas - Mantido como string
* Colunas não informadas foram mantidas como string

In [0]:
df_new = df_listings

In [0]:
# Removendo caracteres

for i in tratar_antes:
    df_new = (df_new
            .withColumn(i, regexp_replace(col(i), "\\$", ""))
            .withColumn(i, regexp_replace(col(i), ",", ""))
            .withColumn(i, regexp_replace(col(i), " ", ""))
            .withColumn(i, regexp_replace(col(i), "\\%", "")))

In [0]:
# Tratamento colunas Integer
for i in numericos_int:
    df_new = df_new.withColumn(i, col(i).cast(IntegerType()))

In [0]:
# Transformar em Float
for i in numericos_float:
    df_new = df_new.withColumn(i, col(i).cast(FloatType()))

In [0]:
# Transformar em LongType
for i in numericos_long:
    df_new = df_new.withColumn(i, col(i).cast(LongType()))

In [0]:
# Transformar em Data
for i in colunas_data:
    df_new = df_new.withColumn(i, to_date(i, "yyyy-MM-dd"))

In [0]:
# Transformar em Booleanos
for i in booleanos:
    df_new = (df_new.withColumn(i, 
                                when(col(i) == "t", True).
                                when(col(i) == "f", False).
                                otherwise(None)
                                ))

In [0]:
df_listings.filter(df_listings.scrape_id == "N/A").count()

In [0]:
df_listings.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in booleanos]).display()

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in booleanos]).display()

## Reviews

In [0]:
df_reviews = spark.read.parquet(path_bronze_reviews)
df_reviews.display()

In [0]:
df_reviews.columns

In [0]:
df_new = (df_reviews
               .withColumn("listing_id", col("listing_id").cast(LongType()))
               .withColumn("id", col("id").cast(LongType()))
               .withColumn("date", to_timestamp("date", "yyyy-MM-dd"))
               .withColumn("reviewer_id", col("reviewer_id").cast(LongType())))

df_new.display()

In [0]:
df_reviews.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_reviews.columns]).display()

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_new.columns]).display()

# Great Expectations

## Calendar

In [0]:
# Calendar
df_calendar = spark.read.parquet(path_silver_calendar)

In [0]:
# Contextos
context_calendar = gx.get_context()

data_source_calendar = context_calendar.data_sources.add_spark("calendar_data_source")

# Data Assets
data_asset_calendar = data_source_calendar.add_dataframe_asset(name="calendar_data_asset")

# Definição de Batches
batch_definition_calendar = data_asset_calendar.add_batch_definition_whole_dataframe("calendar_batch_definition")

# Batches
batch_calendar = batch_definition_calendar.get_batch(batch_parameters={"dataframe": df_calendar})

# Suite
suite_calendar = gx.ExpectationSuite(name="suite_calendar")
suite_calendar = context_calendar.suites.add(suite_calendar)

# Colunas
numericos_int = ["minimum_nights", "maximum_nights"]

numericos_float = ["price", "adjusted_price"]

numericos_long = ["listing_id"]

colunas_data = ["date"]

booleanos = ["available"]

string_lista = [x for x in df_calendar.columns if x not in numericos_int + numericos_float + numericos_long + colunas_data + booleanos]

# Validações
for coluna in numericos_int:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="IntegerType")
  suite_calendar.add_expectation(expectation)

for coluna in numericos_float:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="FloatType")
  suite_calendar.add_expectation(expectation)

for coluna in numericos_long:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="LongType")
  suite_calendar.add_expectation(expectation)

for coluna in colunas_data:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="DateType")
  suite_calendar.add_expectation(expectation)

for coluna in booleanos:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="BooleanType")
  suite_calendar.add_expectation(expectation)

for coluna in string_lista:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="StringType")
  suite_calendar.add_expectation(expectation)

validation_definition_calendar = gx.ValidationDefinition(data=batch_definition_calendar, suite=suite_calendar, name="validacao_calendar")

validation_definition_calendar.run(batch_parameters={"dataframe":df_calendar})

/databricks/python/lib/python3.11/site-packages/ipywidgets/widgets/widget.py:503: DeprecationWarning: The `ipykernel.comm.Comm` class has been deprecated. Please use the `comm` module instead.For creating comms, use the function `from comm import create_comm`.
  self.comm = Comm(**args)


Calculating Metrics:   0%|          | 0/1 [00:00<?, ?it/s]

{
  "success": false,
  "results": [
    {
      "success": true,
      "expectation_config": {
        "type": "expect_column_values_to_be_of_type",
        "kwargs": {
          "batch_id": "calendar_data_source-calendar_data_asset",
          "column": "minimum_nights",
          "type_": "IntegerType"
        },
        "meta": {},
        "id": "50a65541-a46b-42af-86d3-094687772ded"
      },
      "result": {
        "observed_value": "IntegerType"
      },
      "meta": {},
      "exception_info": {
        "raised_exception": false,
        "exception_traceback": null,
        "exception_message": null
      }
    },
    {
      "success": true,
      "expectation_config": {
        "type": "expect_column_values_to_be_of_type",
        "kwargs": {
          "batch_id": "calendar_data_source-calendar_data_asset",
          "column": "maximum_nights",
          "type_": "IntegerType"
        },
        "meta": {},
        "id": "f8178fe6-a3a1-446f-8c9a-d3ba81f49b09"
      },
     

## Listings

In [0]:
# Listings
df_listings = spark.read.parquet(path_silver_listings)

In [0]:
# Contextos
context_listings = gx.get_context()

data_source_listings = context_listings.data_sources.add_spark("listings_data_source")

# Data Assets
data_asset_listings = data_source_listings.add_dataframe_asset(name="listings_data_asset")

# Definição de Batches
batch_definition_listings = data_asset_listings.add_batch_definition_whole_dataframe("listings_batch_definition")

# Batches
batch_listings = batch_definition_listings.get_batch(batch_parameters={"dataframe": df_listings})

# Suite
suite_listings = gx.ExpectationSuite(name="suite_listings")
suite_listings = context_listings.suites.add(suite_listings)

# Colunas

numericos_int = ["host_id", "host_response_rate", "host_listings_count", "host_total_listings_count", 
                 "accommodates", "bedrooms", "beds", "minimum_nights", "maximum_nights", "minimum_minimum_nights", 
                 "maximum_minimum_nights", "minimum_maximum_nights", "maximum_maximum_nights", "availability_30", 
                 "availability_60", "availability_90", "availability_365", "number_of_reviews", "number_of_reviews_ltm", 
                 "number_of_reviews_l30d", "calculated_host_listings_count", "calculated_host_listings_count_entire_homes", 
                 "calculated_host_listings_count_private_rooms", "calculated_host_listings_count_shared_rooms"]

numericos_float = ["latitude", "longitude", "bathrooms", "price", "minimum_nights_avg_ntm", "maximum_nights_avg_ntm", 
                   "review_scores_rating", "review_scores_accuracy", "review_scores_cleanliness", "review_scores_checkin", 
                   "review_scores_communication", "review_scores_location", "review_scores_value", "reviews_per_month"]

numericos_long = ["id", "scrape_id"]

colunas_data = ["last_scraped", "host_since", "calendar_last_scraped", "first_review", "last_review"]

booleanos = ["host_is_superhost", "host_has_profile_pic", "host_identity_verified", "has_availability", "instant_bookable"]

listas = ["host_verifications", "amenities"]

string_lista = [x for x in df_listings.columns if x not in numericos_int + numericos_float + numericos_long + colunas_data + booleanos + listas]

# Validações
for coluna in numericos_int:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="IntegerType")
  suite_listings.add_expectation(expectation)

for coluna in numericos_float:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="FloatType")
  suite_listings.add_expectation(expectation)

for coluna in numericos_long:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="LongType")
  suite_listings.add_expectation(expectation)

for coluna in colunas_data:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="DateType")
  suite_listings.add_expectation(expectation)

for coluna in booleanos:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="BooleanType")
  suite_listings.add_expectation(expectation)

for coluna in listas:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="ListType")
  suite_listings.add_expectation(expectation)

for coluna in string_lista:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="StringType")
  suite_listings.add_expectation(expectation)

# Maior ou igual a 0
for i in numericos_long + numericos_int + [x for x in numericos_float if x not in ["latitude", "longitude"]]:
  expectation = gx.expectations.ExpectColumnValuesToBeBetween(column=i, min_value=0, strict_min=True)
  suite_listings.add_expectation(expectation)

# Rates 0-100
for i in ["host_response_rate", "host_acceptance_rate"]:
  expectation = gx.expectations.ExpectColumnValuesToBeBetween(column=i, min_value=0, max_value=100)
  suite_listings.add_expectation(expectation)

# Rates 0-5
for i in ["review_scores_rating", "review_scores_accuracy", "review_scores_cleanliness", "review_scores_checkin", "review_scores_communication", "review_scores_location", "review_scores_value", "reviews_per_month"]:
  expectation = gx.expectations.ExpectColumnValuesToBeBetween(column=i, min_value=0, max_value=5)
  suite_listings.add_expectation(expectation)

# Datas entre o ano de lançamento do AirBnB e a data atual
today = date.today()
air_bnb_release = date(2008,1,1)
for i in colunas_data:
  expectation = gx.expectations.ExpectColumnValuesToBeBetween(column=i, min_value=air_bnb_release, max_value=today)
  suite_listings.add_expectation(expectation)

# Valores Booleanos
for i in booleanos:
  expectation = gx.expectations.ExpectColumnValuesToBeInSet(column=i, value_set=[True, False])
  suite_listings.add_expectation(expectation)

# Latitude
expectation = gx.expectations.ExpectColumnValuesToBeBetween(column="latitude", min_value=-90, max_value=90)
suite_listings.add_expectation(expectation)

# Longitude
expectation = gx.expectations.ExpectColumnValuesToBeBetween(column="longitude", min_value=-180, max_value=180)
suite_listings.add_expectation(expectation)

validation_definition_listings = gx.ValidationDefinition(data=batch_definition_listings, suite=suite_listings, name="validacao_listings")

validation_definition_listings.run(batch_parameters={"dataframe":df_listings})

INFO:great_expectations.data_context.types.base:Created temporary directory '/tmp/tmpwbezbcf_' for ephemeral docs site
/databricks/python/lib/python3.11/site-packages/ipywidgets/widgets/widget.py:503: DeprecationWarning: The `ipykernel.comm.Comm` class has been deprecated. Please use the `comm` module instead.For creating comms, use the function `from comm import create_comm`.
  self.comm = Comm(**args)


Calculating Metrics:   0%|          | 0/521 [00:00<?, ?it/s]

{
  "success": false,
  "results": [
    {
      "success": true,
      "expectation_config": {
        "type": "expect_column_values_to_be_of_type",
        "kwargs": {
          "batch_id": "listings_data_source-listings_data_asset",
          "column": "host_id",
          "type_": "IntegerType"
        },
        "meta": {},
        "id": "e96e8179-4592-4302-8c7b-f8ce0c6857f8"
      },
      "result": {
        "observed_value": "IntegerType"
      },
      "meta": {},
      "exception_info": {
        "raised_exception": false,
        "exception_traceback": null,
        "exception_message": null
      }
    },
    {
      "success": true,
      "expectation_config": {
        "type": "expect_column_values_to_be_between",
        "kwargs": {
          "batch_id": "listings_data_source-listings_data_asset",
          "column": "host_id",
          "min_value": 0.0,
          "strict_min": true
        },
        "meta": {},
        "id": "b72602e6-2a16-4bd1-ba13-229a5ed5a3e9"
    

## Reviews

In [0]:
# Reviews
df_reviews = spark.read.parquet(path_silver_reviews)

In [0]:
# Contextos
context_reviews = gx.get_context()

data_source_reviews = context_reviews.data_sources.add_spark("reviews_data_source")

# Data Assets
data_asset_reviews = data_source_reviews.add_dataframe_asset(name="reviews_data_asset")

# Definição de Batches
batch_definition_reviews = data_asset_reviews.add_batch_definition_whole_dataframe("reviews_batch_definition")

# Batches
batch_reviews = batch_definition_reviews.get_batch(batch_parameters={"dataframe": df_reviews})

# Suite
suite_reviews = gx.ExpectationSuite(name="suite_reviews")
suite_reviews = context_reviews.suites.add(suite_reviews)

# Colunas
numericos_long = ["listing_id", "id", "reviewer_id"]

colunas_data = ["date"]

string_lista = [x for x in df_reviews.columns if x not in numericos_long + colunas_data]

# Validações
for coluna in numericos_int:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="IntegerType")
  suite_reviews.add_expectation(expectation)

for coluna in numericos_float:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="FloatType")
  suite_reviews.add_expectation(expectation)

for coluna in numericos_long:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="LongType")
  suite_reviews.add_expectation(expectation)

for coluna in colunas_data:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="DateType")
  suite_reviews.add_expectation(expectation)

for coluna in booleanos:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="BooleanType")
  suite_reviews.add_expectation(expectation)

for coluna in string_lista:
  expectation = gx.expectations.ExpectColumnValuesToBeOfType(column=coluna, type_="StringType")
  suite_reviews.add_expectation(expectation)

validation_definition_reviews = gx.ValidationDefinition(data=batch_definition_reviews, suite=suite_reviews, name="validacao_reviews")

validation_definition_reviews.run(batch_parameters={"dataframe":df_reviews})

/databricks/python/lib/python3.11/site-packages/ipywidgets/widgets/widget.py:503: DeprecationWarning: The `ipykernel.comm.Comm` class has been deprecated. Please use the `comm` module instead.For creating comms, use the function `from comm import create_comm`.
  self.comm = Comm(**args)


Calculating Metrics:   0%|          | 0/1 [00:00<?, ?it/s]

{
  "success": false,
  "results": [
    {
      "success": false,
      "expectation_config": {
        "type": "expect_column_values_to_be_of_type",
        "kwargs": {
          "column": "minimum_nights",
          "type_": "IntegerType",
          "batch_id": "reviews_data_source-reviews_data_asset"
        },
        "meta": {},
        "id": "2b1e2f22-3345-42f5-956e-a823f0574d6d"
      },
      "result": {},
      "meta": {},
      "exception_info": {
        "exception_traceback": "Traceback (most recent call last):\n  File \"/local_disk0/.ephemeral_nfs/envs/pythonEnv-a3ac7539-3884-4e03-960a-c15a55be512f/lib/python3.11/site-packages/great_expectations/validator/validator.py\", line 650, in graph_validate\n    result = expectation.metrics_validate(\n             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^\n  File \"/local_disk0/.ephemeral_nfs/envs/pythonEnv-a3ac7539-3884-4e03-960a-c15a55be512f/lib/python3.11/site-packages/great_expectations/expectations/expectation.py\", line 1122, in metrics

# Gold

In [0]:
df_calendar = spark.read.parquet(path_silver_calendar)
df_listings = spark.read.parquet(path_silver_listings)
df_reviews = spark.read.parquet(path_silver_reviews)

In [0]:
calendar_columns = df_calendar.columns
print(calendar_columns)

['listing_id', 'date', 'available', 'price', 'adjusted_price', 'minimum_nights', 'maximum_nights']


In [0]:
listings_columns = df_listings.columns
print(listings_columns)

['id', 'listing_url', 'scrape_id', 'last_scraped', 'source', 'name', 'description', 'neighborhood_overview', 'picture_url', 'host_id', 'host_url', 'host_name', 'host_since', 'host_location', 'host_about', 'host_response_time', 'host_response_rate', 'host_acceptance_rate', 'host_is_superhost', 'host_thumbnail_url', 'host_picture_url', 'host_neighbourhood', 'host_listings_count', 'host_total_listings_count', 'host_verifications', 'host_has_profile_pic', 'host_identity_verified', 'neighbourhood', 'neighbourhood_cleansed', 'neighbourhood_group_cleansed', 'latitude', 'longitude', 'property_type', 'room_type', 'accommodates', 'bathrooms', 'bathrooms_text', 'bedrooms', 'beds', 'amenities', 'price', 'minimum_nights', 'maximum_nights', 'minimum_minimum_nights', 'maximum_minimum_nights', 'minimum_maximum_nights', 'maximum_maximum_nights', 'minimum_nights_avg_ntm', 'maximum_nights_avg_ntm', 'calendar_updated', 'has_availability', 'availability_30', 'availability_60', 'availability_90', 'availabil

In [0]:
reviews_columns = df_reviews.columns
print(reviews_columns)

['listing_id', 'id', 'date', 'reviewer_id', 'reviewer_name', 'comments']


# Requisicoes para Raw

In [0]:
!pip install bs4

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

In [0]:
link_listings = "https://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2024-06-27/data/listings.csv.gz"
link_calendar = "https://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2024-06-27/data/calendar.csv.gz"
link_reviews = "https://data.insideairbnb.com/brazil/rj/rio-de-janeiro/2024-06-27/data/reviews.csv.gz"

url = "https://insideairbnb.com/get-the-data/"

response  = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")

url_listings = [a['href'] for a in soup.find_all('a', href=True) if "rio-de-janeiro" in a['href'] and "/data/listings.csv.gz" in a['href']][0]
url_calendar = [a['href'] for a in soup.find_all('a', href=True) if "rio-de-janeiro" in a['href'] and "/data/calendar.csv.gz" in a['href']][0]
url_reviews = [a['href'] for a in soup.find_all('a', href=True) if "rio-de-janeiro" in a['href'] and "/data/reviews.csv.gz" in a['href']][0]


In [0]:
# Caminho do Projeto
path_projeto = "/FileStore/Projeto_Analytics"

# Arquivos
listings = "listings_csv.gz"
calendar = "calendar_csv.gz"
reviews = "reviews_csv.gz"

# Caminho Bruto
path_raw = "/FileStore/Projeto_Analytics/data/raw"
path_raw_listings = f"/FileStore/Projeto_Analytics/data/raw/{listings}"
path_raw_calendar = f"/FileStore/Projeto_Analytics/data/raw/{calendar}"
path_raw_reviews = f"/FileStore/Projeto_Analytics/data/raw/{reviews}"

# Caminho Bronze
path_bronze = "/FileStore/Projeto_Analytics/data/bronze/"
path_bronze_listings = "/FileStore/Projeto_Analytics/data/bronze/listings"
path_bronze_calendar = "/FileStore/Projeto_Analytics/data/bronze/calendar"
path_bronze_reviews = "/FileStore/Projeto_Analytics/data/bronze/reviews"

# Caminho Silver
path_silver = "/FileStore/Projeto_Analytics/data/silver/"
path_silver_listings = "/FileStore/Projeto_Analytics/data/silver/listings"
path_silver_calendar = "/FileStore/Projeto_Analytics/data/silver/calendar"
path_silver_reviews = "/FileStore/Projeto_Analytics/data/silver/reviews"

# Database
name_db = "projeto_ae"


In [0]:


dfp = pd.read_csv(link_listings)
dfp.display()

/databricks/spark/python/pyspark/sql/pandas/utils.py:51: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(pandas.__version__) < LooseVersion(minimum_pandas_version):
/databricks/spark/python/pyspark/sql/pandas/utils.py:85: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(pyarrow.__version__) < LooseVersion(minimum_pyarrow_version):


id listing_url scrape_id last_scraped source name description neighborhood_overview picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed latitude longitude property_type room_type accommodates bathrooms bathrooms_text bedrooms beds amenities price minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm number_of_reviews_l30d first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value license instant_bookable calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 17878 https://www.airbnb.com/rooms/17878 20240627045056 2024-06-28 city scrape Very Nice 2Br in Copacabana w. balcony, fast WiFi Please note that elevated rates applies for New Years and Carnival. Price depends on length of stay and number of people. Generally I prefer a stay for 1 week or more and a maximum of 5 people (6 at the most). Contact me, and we will discuss. - Bright and sunny - Large balcony (25 square meters) - High speed WiFi (up to 500MB) - Smart TV (you can watch Netflix etc. if you have an account) - 24h doorman - 1 minute to walk to Copacabana Beach - Silent "split" air conditioning - Best spot in Rio This is the one of the bests spots in Rio. Because of the large balcony and proximity to the beach, it has huge advantages in the current situation. https://a0.muscache.com/pictures/65320518/30698f38_original.jpg 68997 https://www.airbnb.com/users/show/68997 Matthias 2010-01-08 Rio de Janeiro, Brazil I am a journalist/writer. Lived in NYC for 15 years. I am now based in Rio and published 3 volumes of travel stories on AMAZ0N: "The World Is My Oyster". If you have never been to Rio, check out the first story, and you'll get an idea. Apart from Rio, you'll find 29 other travel stories from all around the globe. within an hour 100% 100% t https://a0.muscache.com/im/pictures/user/67b13cea-8c11-49c0-a08d-7f42c330676e.jpg?aki_policy=profile_small https://a0.muscache.com/im/pictures/user/67b13cea-8c11-49c0-a08d-7f42c330676e.jpg?aki_policy=profile_x_medium Copacabana 2 5 ['email', 'phone'] t t Rio de Janeiro, Brazil Copacabana null -22.96599 -43.1794 Entire condo Entire home/apt 5 1.0 1 bath 2.0 2.0 ["Smoking allowed", "Essentials", "Air conditioning", "Hangers", "Building staff", "Kitchen", "Refrigerator", "Bathtub", "Dishes and silverware", "Hot water", "Microwave", "Elevator", "Luggage dropoff allowed", "Coffee maker", "Bed linens", "Private entrance", "Hair dryer", "Iron", "Self check-in", "Oven", "Stove", "Patio or balcony", "TV with standard cable", "Cooking basics", "Wifi", "Paid parking off premises"] $310.00 5 28 5 5 28 28 5.0 28.0 null t 6 32 51 274 2024-06-28 319 23 1 2010-07-15 2024-06-08 4.71 4.77 4.64 4.84 4.91 4.77 4.67 null f 1 1 0 0 1.88 25026 https://www.airbnb.com/rooms/25026 20240627045056 2024-06-28 city scrape Beautiful Modern Decorated Studio in Copa **Fully renovated in Dec 2022, new kitchen, new bathroom, new flooring! ** ** The apartment was all renovated, floor, bathroom and new kitchen in Dec 2022!** If you don't have any information on Airbnb and have never used it before, please message them first to let them know who you are. Our apartment is a little gem, everyone loves staying there! Best 